In [1]:
from XRDXRFutils import PhaseBlock, PhaseRow, DatabaseXRD, DataXRD, SpectraXRD, GaussNewton, PhaseList, PhaseMap, PhaseSearch, PhaseMapSave

import os
import pickle

from XRDXRFutils import snip3d,convolve3d

from joblib import Parallel, delayed
import h5py
from sklearn.linear_model import LinearRegression
from scipy.optimize import curve_fit, least_squares

from scipy.signal import windows

from numpy import arange,linspace,concatenate,sqrt,log,histogram,newaxis,pad,fft,array,asarray,array_split
from matplotlib.pyplot import fill_between,sca,legend,imshow,subplots,plot,xlim,ylim,xlabel,ylabel,cm,title,scatter,colorbar,figure,vlines
from sklearn.cluster import KMeans,MiniBatchKMeans

from PIL import Image

import gc

from multiprocessing import Process,Queue

from joblib import Parallel,delayed

import threading

In [2]:
path_xrd = '/home/shared/dataXRDXRF/MunchMuseum/M491/ProfiloXRD/'
path_database = '/home/shared/DatabaseXRD'

In [3]:
%%time
try:
    data = DataXRD().load_h5(path_xrd + 'xrd.h5')
except:
    print('Reading from raw data.')
    data = DataXRD().read_params(path_xrd + 'Scanning_Parameters.txt').read(path_xrd).calibrate_from_file(path_xrd + 'calibration.ini').remove_background().save_h5(path_xrd + 'xrd.h5')

Loading: /home/shared/dataXRDXRF/MunchMuseum/M491/ProfiloXRD/xrd.h5
CPU times: user 4.32 ms, sys: 130 ms, total: 134 ms
Wall time: 133 ms


In [4]:
database = DatabaseXRD().read_cifs(path_database)
print('Phases in database:',len(database))

Phases in database: 137


In [5]:
lazurite = database['Lazurite'][0]
hydrocerussite = database['Hydrocerussite'][0]
cinnabar = database['Cinnabar'][1]
barite = database['Barite'][0]
spinel = database['Spinel'][0]
calcite = database['Calcite'][0]
hematite = database['Hematite'][4]

phases = PhaseList([hydrocerussite,lazurite,cinnabar])

min_theta = 20
max_theta = 53
min_intensity = 0.1
first_n_peaks = None

phases.get_theta(min_intensity=min_intensity,
                 min_theta = min_theta,
                 max_theta = max_theta,
                first_n_peaks = first_n_peaks)

(array([20.93971943, 24.69207474, 27.18665762, 34.04367108, 34.18152332,
        40.42823653, 42.6228012 , 43.04402736, 44.21036078, 48.24071298,
        49.014125  , 23.94038756, 31.06153655, 34.11266972, 42.10609553,
        26.51331315, 28.15070761, 31.19598604, 43.62074332, 45.75881859,
        51.77486834, 52.72567416]),
 array([0.27071, 0.74861, 1.     , 0.34109, 0.53856, 0.24343, 0.14858,
        0.18136, 0.18249, 0.12698, 0.29295, 1.     , 0.11682, 0.27028,
        0.13034, 0.76186, 0.219  , 1.     , 0.37672, 0.32453, 0.11862,
        0.2239 ]))

In [6]:
data.data.shape

(95, 170, 1280)

In [7]:
%%time
spectra = []
for i in range(data.data.shape[0]):
    for j in range(data.data.shape[1]):
        spectra += [SpectraXRD().from_Data(data,i,j)]
        
spectra = array_split(spectra,26)

CPU times: user 158 ms, sys: 50.9 ms, total: 209 ms
Wall time: 207 ms


In [8]:
def build_blocks(block_spectra,phases):
    return PhaseBlock(block_spectra,phases)

In [9]:
def search_blocks(phase_block):
    return phase_block.search()

In [10]:
%%time
out = Parallel(n_jobs=26,
               prefer='processes',
               #pre_dispatch='all',
               verbose=100,
               backend='multiprocessing',
               mmap_mode=None,
               max_nbytes=None
              )(
    delayed(build_blocks)(block_spectra,phases) for block_spectra in spectra
)

[Parallel(n_jobs=26)]: Using backend MultiprocessingBackend with 26 concurrent workers.
[Parallel(n_jobs=26)]: Done   1 tasks      | elapsed:    2.0s
[Parallel(n_jobs=26)]: Done   2 out of  26 | elapsed:    2.5s remaining:   30.2s
[Parallel(n_jobs=26)]: Done   3 out of  26 | elapsed:    2.8s remaining:   21.6s
[Parallel(n_jobs=26)]: Done   4 out of  26 | elapsed:    3.0s remaining:   16.8s
[Parallel(n_jobs=26)]: Done   5 out of  26 | elapsed:    3.2s remaining:   13.5s
[Parallel(n_jobs=26)]: Done   6 out of  26 | elapsed:    3.4s remaining:   11.4s
[Parallel(n_jobs=26)]: Done   7 out of  26 | elapsed:    3.5s remaining:    9.6s
[Parallel(n_jobs=26)]: Done   8 out of  26 | elapsed:    3.7s remaining:    8.3s
[Parallel(n_jobs=26)]: Done   9 out of  26 | elapsed:    3.8s remaining:    7.2s
[Parallel(n_jobs=26)]: Done  10 out of  26 | elapsed:    4.0s remaining:    6.4s
[Parallel(n_jobs=26)]: Done  11 out of  26 | elapsed:    4.2s remaining:    5.7s
[Parallel(n_jobs=26)]: Done  12 out of  

In [21]:
out

NameError: name 'out' is not defined

In [19]:
del out

In [23]:
gc.collect()

0

In [11]:
%%time
out = Parallel(n_jobs=26,
               prefer='processes',
               #pre_dispatch='n_jobs',
               verbose=100,
               backend='multiprocessing',
               #backend='loky'
               #mmap_mode=None,
               #max_nbytes=None
              )(
    delayed(search_blocks)(phase_block) for phase_block in out
)

[Parallel(n_jobs=26)]: Using backend MultiprocessingBackend with 26 concurrent workers.
[Parallel(n_jobs=26)]: Done   1 tasks      | elapsed:   45.8s
[Parallel(n_jobs=26)]: Done   2 out of  26 | elapsed:   46.0s remaining:  9.2min
[Parallel(n_jobs=26)]: Done   3 out of  26 | elapsed:   46.3s remaining:  5.9min
[Parallel(n_jobs=26)]: Done   4 out of  26 | elapsed:   46.6s remaining:  4.3min
[Parallel(n_jobs=26)]: Done   5 out of  26 | elapsed:   46.8s remaining:  3.3min
[Parallel(n_jobs=26)]: Done   6 out of  26 | elapsed:   47.1s remaining:  2.6min
[Parallel(n_jobs=26)]: Done   7 out of  26 | elapsed:   47.4s remaining:  2.1min
[Parallel(n_jobs=26)]: Done   8 out of  26 | elapsed:   47.7s remaining:  1.8min
[Parallel(n_jobs=26)]: Done   9 out of  26 | elapsed:   48.7s remaining:  1.5min
[Parallel(n_jobs=26)]: Done  10 out of  26 | elapsed:   48.9s remaining:  1.3min
[Parallel(n_jobs=26)]: Done  11 out of  26 | elapsed:   49.3s remaining:  1.1min
[Parallel(n_jobs=26)]: Done  12 out of  

In [13]:
gc.collect()

91

In [12]:
out

[[[<XRDXRFutils.gaussnewton.GaussNewton at 0x7fd3a7e20160>,
 [[<XRDXRFutils.gaussnewton.GaussNewton at 0x7fd3ad906430>,
 [[<XRDXRFutils.gaussnewton.GaussNewton at 0x7fd4004ce0d0>,
 [[<XRDXRFutils.gaussnewton.GaussNewton at 0x7fd3a6ae0550>,
 [[<XRDXRFutils.gaussnewton.GaussNewton at 0x7fd3ac7c3910>,
 [[<XRDXRFutils.gaussnewton.GaussNewton at 0x7fd3c0719340>,
 [[<XRDXRFutils.gaussnewton.GaussNewton at 0x7fd3ac163dc0>,
 [[<XRDXRFutils.gaussnewton.GaussNewton at 0x7fd3a5efe130>,
 [[<XRDXRFutils.gaussnewton.GaussNewton at 0x7fd3a7d94100>,
 [[<XRDXRFutils.gaussnewton.GaussNewton at 0x7fd3a5592e50>,
 [[<XRDXRFutils.gaussnewton.GaussNewton at 0x7fd3a549a910>,
 [[<XRDXRFutils.gaussnewton.GaussNewton at 0x7fd3a7d8ab20>,
 [[<XRDXRFutils.gaussnewton.GaussNewton at 0x7fd3a7d940a0>,
 [[<XRDXRFutils.gaussnewton.GaussNewton at 0x7fd3a7d8a7f0>,
 [[<XRDXRFutils.gaussnewton.GaussNewton at 0x7fd3a49d9dc0>,
 [[<XRDXRFutils.gaussnewton.GaussNewton at 0x7fd3a4422ee0>,
 [[<XRDXRFutils.gaussnewton.GaussNewton 

In [7]:
def getsp(block_spectra,phases):
    
    print(len(block_spectra))
    
    return block_spectra,phases

In [8]:
def getblock(block_spectra,phases):
    
    block = PhaseBlock(block_spectra,phases)
    #block.search()
    print(block)
    print(len(block))
    
    return block

In [9]:
def runblock(phaseblock):
    
    p = phaseblock
    
    print('Search')
    print(p.__class__)
    p.search()
    print('Finished')

In [11]:
%%time
pb = [PhaseBlock(block_spectra,phases) for block_spectra in spectra]

CPU times: user 23.2 s, sys: 401 ms, total: 23.6 s
Wall time: 22.6 s


In [10]:
%%time
out = Parallel(n_jobs=26,
               prefer='processes',
               pre_dispatch='all',
               verbose=100,
               mmap_mode=None,
               max_nbytes=None)(
    delayed(getblock)(block_spectra,phases) for block_spectra in spectra
)

[Parallel(n_jobs=26)]: Using backend LokyBackend with 26 concurrent workers.
[Parallel(n_jobs=26)]: Done   1 out of  26 | elapsed:   54.8s remaining: 22.9min
[Parallel(n_jobs=26)]: Done   2 out of  26 | elapsed:   55.4s remaining: 11.1min
[Parallel(n_jobs=26)]: Done   3 out of  26 | elapsed:   55.7s remaining:  7.1min
[Parallel(n_jobs=26)]: Done   4 out of  26 | elapsed:   55.9s remaining:  5.1min
[Parallel(n_jobs=26)]: Done   5 out of  26 | elapsed:   56.3s remaining:  3.9min
[Parallel(n_jobs=26)]: Done   6 out of  26 | elapsed:   56.6s remaining:  3.1min
[Parallel(n_jobs=26)]: Done   7 out of  26 | elapsed:   56.8s remaining:  2.6min
[Parallel(n_jobs=26)]: Done   8 out of  26 | elapsed:   57.1s remaining:  2.1min
[Parallel(n_jobs=26)]: Done   9 out of  26 | elapsed:   57.3s remaining:  1.8min
[Parallel(n_jobs=26)]: Done  10 out of  26 | elapsed:   57.7s remaining:  1.5min
[Parallel(n_jobs=26)]: Done  11 out of  26 | elapsed:   58.0s remaining:  1.3min
[Parallel(n_jobs=26)]: Done  12 

In [37]:
gc.collect()

0

In [15]:
hex(id(out[0][0][0].mu)),hex(id(out[0][2][0].mu))

('0x7f5735f68c90', '0x7f5735f68c90')

In [30]:
out[0].__sizeof__(),out[0][0].__sizeof__(),out[0][0][0].__sizeof__(),spectra.__sizeof__()

(5048, 120, 32, 296)

In [34]:
out[0]

[[<XRDXRFutils.gaussnewton.GaussNewton at 0x7f573eec8fa0>,

In [8]:
len(spectra[0])

323

In [9]:
%%time
x = PhaseBlock(spectra[0],phases,
               sigma_initial = 0.2,
               min_theta = min_theta,
               max_theta = max_theta,
               min_intensity = min_intensity,
               first_n_peaks = first_n_peaks
              )

CPU times: user 493 ms, sys: 9.07 ms, total: 502 ms
Wall time: 477 ms


In [10]:
%%time
x.search()

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

[[<XRDXRFutils.gaussnewton.GaussNewton at 0x7f8e9688e7c0>,

In [1]:
def run(block_spectra,phases):
    x = PhaseBlock(block_spectra, phases,
                   sigma_init = 0.2,
                    min_theta = min_theta,
                    max_theta = max_theta,
                    min_intensity = min_intensity,
                    first_n_peaks = first_n_peaks)
    #x.search()
    
    return x
    

In [ ]:
%%time
out = Parallel(n_jobs=50,
               prefer='processes',
               batch_size='auto',mmap_mode=None,
               max_nbytes=None)(delayed(run)(block_spectra,phases,
                                             min_theta = 20,
                                             max_theta = 53,
                                             min_intensity = 0.1,
                                             first_n_peaks = None) for block_spectra in spectra)

In [7]:
%%time
prow = PhaseRow(data, phases, 50,
                    min_theta = min_theta,
                    max_theta = max_theta,
                    min_intensity = min_intensity,
                    first_n_peaks = first_n_peaks)

CPU times: user 161 ms, sys: 5.13 ms, total: 167 ms
Wall time: 159 ms


In [7]:
def run(data,phases,i):
    x = PhaseRow(data, phases, i,
                    min_theta = min_theta,
                    max_theta = max_theta,
                    min_intensity = min_intensity,
                    first_n_peaks = first_n_peaks)
    x.search()
    
    return x
    

In [18]:
out[0][0][1]

In [22]:
gc.collect()

0

In [10]:
def worker(q,data,phases,i):
    prow = PhaseRow(data,phases,i,
                    min_theta = 20,
                    max_theta = 53,
                    min_intensity = 0.1,
                    first_n_peaks = None)
    prow.search()
    q.put(prow)

In [11]:
%%time
q = Queue()

p = []

for i in range(169):
    p += [Process(target=worker,args = (q,data, phases, i))]

for x in p:
    x.start()
    
out = []
for x in p:
    out += [q.get()]
for x in p:
    x.join()

CPU times: user 7.36 s, sys: 10.5 s, total: 17.8 s
Wall time: 2min 32s


In [12]:
out

[[[<XRDXRFutils.gaussnewton.GaussNewton at 0x7ff385c2b820>,
 [[<XRDXRFutils.gaussnewton.GaussNewton at 0x7ff3c8285af0>,
 [[<XRDXRFutils.gaussnewton.GaussNewton at 0x7ff3c82a6940>,
 [[<XRDXRFutils.gaussnewton.GaussNewton at 0x7ff385c300d0>,
 [[<XRDXRFutils.gaussnewton.GaussNewton at 0x7ff385c30100>,
 [[<XRDXRFutils.gaussnewton.GaussNewton at 0x7ff385c30400>,
 [[<XRDXRFutils.gaussnewton.GaussNewton at 0x7ff385c370d0>,
 [[<XRDXRFutils.gaussnewton.GaussNewton at 0x7ff385c37100>,
 [[<XRDXRFutils.gaussnewton.GaussNewton at 0x7ff385c372e0>,
 [[<XRDXRFutils.gaussnewton.GaussNewton at 0x7ff385c3d040>,
 [[<XRDXRFutils.gaussnewton.GaussNewton at 0x7ff385c3d0a0>,
 [[<XRDXRFutils.gaussnewton.GaussNewton at 0x7ff385c3d0d0>,
 [[<XRDXRFutils.gaussnewton.GaussNewton at 0x7ff385c3d5b0>,
 [[<XRDXRFutils.gaussnewton.GaussNewton at 0x7ff385c45070>,
 [[<XRDXRFutils.gaussnewton.GaussNewton at 0x7ff385c450a0>,
 [[<XRDXRFutils.gaussnewton.GaussNewton at 0x7ff385c453a0>,
 [[<XRDXRFutils.gaussnewton.GaussNewton 

In [13]:
o = out[0]
hex(id(o[0][0].I)),hex(id(o[10][0].I))

('0x7ff385c2d0f0', '0x7ff385c2d0f0')

In [14]:
o = out[1]
hex(id(o[0][0].I)),hex(id(o[10][0].I))

('0x7ff385c32270', '0x7ff385c32270')

In [9]:
%%time

pr = []

for i in range(data.shape[1]):
    prow = PhaseRow(data, phases, i,
                    min_theta = min_theta,
                    max_theta = max_theta,
                    min_intensity = min_intensity,
                    first_n_peaks = first_n_peaks)

CPU times: user 21.3 s, sys: 11.9 ms, total: 21.3 s
Wall time: 21.3 s


In [16]:
len(prow)

95

In [6]:
%%time
pm = PhaseMap(data, phases, min_theta = min_theta, max_theta = max_theta, min_intensity = min_intensity, first_n_peaks = first_n_peaks)

sigma initial: 0.2
CPU times: user 21.7 s, sys: 86 ms, total: 21.8 s
Wall time: 21.7 s


AttributeError: 'list' object has no attribute 'search'

In [14]:
%%time
pm.search()

CPU times: user 1min 27s, sys: 10.6 s, total: 1min 38s
Wall time: 2min 25s


In [44]:
pm.list_phase_search[:10]

[[<XRDXRFutils.gaussnewton.GaussNewton at 0x7fb28dc9a6d0>,

In [36]:
hex(id(pm.list_phase_search[0][0].I)),hex(id(pm.list_phase_search[1][0].I))

('0x7fb28e018e10', '0x7fb28dc6b0f0')

In [41]:
pm.list_phase_search[0].spectrum

In [36]:
%%time

p = []

for i in range(data.data.shape[0]):
    for j in range(data.data.shape[1]):
        spectrum = SpectraXRD().from_Data(data,i,j)
        
        p += [PhaseSearch(phases,spectrum)]
        

CPU times: user 14.6 s, sys: 81.5 ms, total: 14.7 s
Wall time: 14.7 s
